
| ![nsdf](https://www.sci.utah.edu/~pascucci/public/NSDF-smaller.PNG)  | [National Science Data Fabric](https://nationalsciencedatafabric.org/) [Jupyter notebook](https://jupyter.org/) <br> created by  [Valerio Pascucci](http://cedmav.com/) and  [Giorgio Scorzelli](https://www.sci.utah.edu/people/scrgiorgio.html)  |   ![CEDMAV](https://www.sci.utah.edu/~pascucci/public/cedmav-small.png)  |   ![SCI](https://www.sci.utah.edu/~pascucci/public/SCI-logo-small.png)  |
|---|:---:|:---:|:---:|
| <img src="https://www.sci.utah.edu/~pascucci/public/seal-storage-small.png"  height="50">| 200TB of cloud space provided by [Seal Storage](https://www.sealstorage.io/)  |   ![NASA](https://www.sci.utah.edu/~pascucci/public/NASA_logo_small.png)| Climate data provided by  [NASA](https://gmao.gsfc.nasa.gov/global_mesoscale/dyamond_phaseII/)  |     |


#  <center> This is a preview of the 200TB data visualized interactively below:
![Visualization of Covid-19 cases](https://www.sci.utah.edu/~pascucci/public/NSDF-NASA.gif)

# Import Bokeh

In [1]:
import os,sys,logging,time
import numpy as np

print(sys.executable)

os.environ["BOKEH_ALLOW_WS_ORIGIN"]="*"
os.environ["BOKEH_LOG_LEVEL"]="debug"
os.environ["VISUS_CPP_VERBOSE"]="0"
os.environ["VISUS_NETSERVICE_VERBOSE"]="0"
os.environ["VISUS_VERBOSE_DISKACCESS"]="0"

import panel as pn
pn.extension(log_level="DEBUG",notifications=True, sizing_mode="stretch_width")

if True:
    sys.path.append("c:/projects/openvisus/build/RelWithDebInfo")
    sys.path.append("c:/projects/openvisuspy/src")

from openvisuspy import Slice, SetupJupyterLogger, LoadDataset, ExecuteBoxQuery
logger=SetupJupyterLogger(logging_level=logging.DEBUG) 
print(time.time(),"OpenVisus imported")

C:\projects\openvisuspy\.venv\Scripts\python.exe


NotificationArea()

1707237684.5649085 OpenVisus imported


In [2]:
button = pn.widgets.Button(name="Is Panel working? Click me...")
def onClick(evt):
    button.name="Yes"
button.on_click(onClick)
app=pn.Row(button)
app

Row(sizing_mode='stretch_width')
    [0] Button(name='Is Panel working? C..., sizing_mode='stretch_width')

# Load Dataset and compute range

In [3]:
access_key="any"
secret_key="any"
endpoint_url="https://maritime.sealstorage.io/api/v0/s3"
key="utah/nasa/dyamond/mit_output/llc2160_arco/visus.idx"
cached="idx"

url="".join([
    f"{endpoint_url}/{key}?",
    f"&access_key={access_key}"
    f"&secret_key={secret_key}"
    f"&endpoint_url={endpoint_url}"
    f"&cached={cached}"
])

db=LoadDataset(url)
W,H,D=db.getLogicBox()[1]
print("logic box",W,H,D)
access=db.createAccess()

# get a Z slice in the middle to compute the range of the data
endh=db.getMaxResolution()-6
Z=D//2
logic_box, delta, num_pixels=db.getAlignedBox([[0,0,Z],[W,H,Z]], endh, slice_dir=2)
data=list(ExecuteBoxQuery(db, access=access, logic_box=logic_box,  endh=endh, num_refinements=1))[0]['data']
palette_range = np.min(data)/4, np.max(data)/4   
print("palette_range",palette_range)

logic box 8640 6480 90
palette_range (-0.25256651639938354, 0.3600933849811554)


In [4]:
def MyApp(timestep=2015, timestep_delta=10,height=800):
    view=Slice()
    view.setScene(url)
    view.setPalette("colorcet.coolwarm")
    view.setPaletteRange(palette_range)
    view.setTimestepDelta(timestep_delta)
    view.setTimestep(timestep)
    view.setField(view.getField())
    view.setResolution(view.getMaxResolution()-6)
    # view.setLogicToPhysic([(0.0,1.0), (0.0,1.0), (0.0,30.0)])
    view.setDirection(2)
    view.setOffset(0)
    return pn.Column(view.getMainLayout(),sizing_mode="stretch_width",height=height)

app=MyApp()
app

Column(height=800, sizing_mode='stretch_width')
    [0] Column(sizing_mode='stretch_both')
        [0] Column(sizing_mode='stretch_both')
            [0] Row(sizing_mode='stretch_width')
                [0] Row(sizing_mode='stretch_width')
                    [0] MenuButton(button_type='primary', items=[['Load/Save', ...], name='File', width=120)
                    [1] TextInput(sizing_mode='stretch_width', visible=False)
                [1] Select(name='view Mode', options=['1', 'probe', ...], value='1', width=80)
                [2] Select(name='Dataset', options=['https://maritime.sealsto...], value='https://maritime.sealstor..., width=180)
                [3] EditableFloatSlider(end=10365, format=NumeralTickFormatter(id='3..., name='Time', sizing_mode='stretch_width', step=1, value=2015)
                [4] Select(name='Speed', options=['1x', '2x', '4x', ...], value='1x', width=60)
                [5] Select(name='Field', options=['u'], value='u', width=80)
                [6] ColorMap(name='Palette', ncols=5, options={'Blues256': ('#08306b', ...}, sizing_mode='stretch_width', value=('#440154', '#440255', ..., value_name='colorcet.coolwarm')
                [7] Select(name='Mapper', options=['linear', 'log'], value='linear', width=80)
                [8] IntSlider(end=34, name='Max Res', sizing_mode='stretch_width', start=20, value=28)
                [9] Checkbox(name='Auto Res', sizing_mode='stretch_width', value=True)
                [10] IntSlider(end=4, name='#Ref', value=2, width=80)
                [11] TextInput(sizing_mode='stretch_width', visible=False)
            [1] GridBox(ncols=1, sizing_mode='stretch_both')
                [0] Row(sizing_mode='stretch_both')
                    [0] Column(sizing_mode='stretch_both')
                        [0] Row(sizing_mode='stretch_width')
                            [0] Select(name='Direction', options={'X': 0, 'Y': 1, 'Z': 2}, value=2, width=80)
                            [1] EditableFloatSlider(end=89, format=NumeralTickFormatter(id='e..., name='Offset', sizing_mode='stretch_width', step=1)
                            [2] Select(name='Range', options=['metadata', 'user', ...], value='dynamic-acc', width=120)
                            [3] FloatInput(disabled=True, name='Min', value=-0.25256651639938354, width=80)
                            [4] FloatInput(disabled=True, name='Max', value=0.3600933849811554, width=80)
                        [1] Row(sizing_mode='stretch_both')
                            [0] Row(sizing_mode='stretch_both')
                                [0] Bokeh(figure, sizing_mode='stretch_width')
                        [2] Row(sizing_mode='stretch_width')
                            [0] TextInput(sizing_mode='stretch_width')
                            [1] TextInput(sizing_mode='stretch_width')
                    [1] Column(sizing_mode='stretch_both', visible=False)
                        [0] Row(sizing_mode='stretch_width')
                            [0] EditableFloatSlider(format=NumeralTickFormatter(id='d..., name='X coordinate', step=1.0, width=160)
                            [1] EditableFloatSlider(format=NumeralTickFormatter(id='f..., name='Y coordinate', step=1, width=160)
                            [2] EditableRangeSlider(format=NumeralTickFormatter(id='2..., name='Range', width=250)
                            [3] RadioButtonGroup(options=['avg', 'mM', 'med', '*'], sizing_mode='stretch_width', value='avg')
                            [4] IntSlider(end=99, name='Res', start=20, value=24, width=100)
                            [5] IntSlider(end=8, name='#x', start=1, value=2, width=80)
                            [6] IntSlider(end=8, name='#y', start=1, value=2, width=80)
                        [1] Row(sizing_mode='stretch_width')
                            [0] Button(name='lime', sizing_mode='stretch_width')
                            [1] Button(name='red', sizing_mode='stretch_width')
                            [2] Button(name

# bellows_CT_NASA_JHochhalter

In [5]:
def MyApp(height=800):
    view=Slice() 
    view.setScene("http://atlantis.sci.utah.edu/mod_visus?dataset=bellows_CT_NASA_JHochhalter&cached=idx") 
    view.setPalette("Greys256")
    view.setPaletteRange((0,65536))
    return pn.Column(view.getMainLayout(),height=height,sizing_mode='stretch_width')

app=MyApp()
app

Column(height=800, sizing_mode='stretch_width')
    [0] Column(sizing_mode='stretch_both')
        [0] Column(sizing_mode='stretch_both')
            [0] Row(sizing_mode='stretch_width')
                [0] Row(sizing_mode='stretch_width')
                    [0] MenuButton(button_type='primary', items=[['Load/Save', ...], name='File', width=120)
                    [1] TextInput(sizing_mode='stretch_width', visible=False)
                [1] Select(name='view Mode', options=['1', 'probe', ...], value='1', width=80)
                [2] Select(name='Dataset', options=['http://atlantis.sci.utah...], value='http://atlantis.sci.utah...., width=180)
                [3] EditableFloatSlider(end=0, format=NumeralTickFormatter(id='b..., name='Time', sizing_mode='stretch_width', step=1)
                [4] Select(name='Speed', options=['1x', '2x', '4x', ...], value='1x', width=60)
                [5] Select(name='Field', options=['data'], value='data', width=80)
                [6] ColorMap(name='Palette', ncols=5, options={'Blues256': ('#08306b', ...}, sizing_mode='stretch_width', value=('#000000', '#010101', ..., value_name='Greys256')
                [7] Select(name='Mapper', options=['linear', 'log'], value='linear', width=80)
                [8] IntSlider(end=30, name='Max Res', sizing_mode='stretch_width', start=20, value=24)
                [9] Checkbox(name='Auto Res', sizing_mode='stretch_width', value=True)
                [10] IntSlider(end=4, name='#Ref', value=2, width=80)
                [11] TextInput(sizing_mode='stretch_width', visible=False)
            [1] GridBox(ncols=1, sizing_mode='stretch_both')
                [0] Row(sizing_mode='stretch_both')
                    [0] Column(sizing_mode='stretch_both')
                        [0] Row(sizing_mode='stretch_width')
                            [0] Select(name='Direction', options={'X': 0, 'Y': 1, 'Z': 2}, value=2, width=80)
                            [1] EditableFloatSlider(end=977, format=NumeralTickFormatter(id='c..., name='Offset', sizing_mode='stretch_width', step=1, value=489)
                            [2] Select(name='Range', options=['metadata', 'user', ...], value='dynamic-acc', width=120)
                            [3] FloatInput(disabled=True, name='Min', width=80)
                            [4] FloatInput(disabled=True, name='Max', value=65536, width=80)
                        [1] Row(sizing_mode='stretch_both')
                            [0] Row(sizing_mode='stretch_both')
                                [0] Bokeh(figure, sizing_mode='stretch_width')
                        [2] Row(sizing_mode='stretch_width')
                            [0] TextInput(sizing_mode='stretch_width')
                            [1] TextInput(sizing_mode='stretch_width')
                    [1] Column(sizing_mode='stretch_both', visible=False)
                        [0] Row(sizing_mode='stretch_width')
                            [0] EditableFloatSlider(format=NumeralTickFormatter(id='b..., name='X coordinate', step=1.0, width=160)
                            [1] EditableFloatSlider(format=NumeralTickFormatter(id='b..., name='Y coordinate', step=1, width=160)
                            [2] EditableRangeSlider(format=NumeralTickFormatter(id='2..., name='Range', width=250)
                            [3] RadioButtonGroup(options=['avg', 'mM', 'med', '*'], sizing_mode='stretch_width', value='avg')
                            [4] IntSlider(end=99, name='Res', start=20, value=24, width=100)
                            [5] IntSlider(end=8, name='#x', start=1, value=2, width=80)
                            [6] IntSlider(end=8, name='#y', start=1, value=2, width=80)
                        [1] Row(sizing_mode='stretch_width')
                            [0] Button(name='lime', sizing_mode='stretch_width')
                            [1] Button(name='red', sizing_mode='stretch_width')
                            [2] Button(name='green', sizing_mode='stretch_width')
         

# NASA Dyamond

In [9]:
def MyApp(height=800):
    
    os.environ["AWS_ACCESS_KEY_ID"]="any"
    os.environ["AWS_SECRET_ACCESS_KEY"]="any"
    os.environ["AWS_ENDPOINT_URL"]="https://maritime.sealstorage.io/api/v0/s3"

    view=Slice()
    view.setScenes({"scenes": [
        {
            "name":str(zone), 
            "url": f"https://maritime.sealstorage.io/api/v0/s3/utah/nasa/dyamond/idx_arco/face{zone}/u_face_{zone}_depth_52_time_0_10269.idx?cached=1"
        }
        for zone in range(6)
    ]})
    view.setResolution(view.getMaxResolution()-3)
    view.setPalette("Turbo256") 
    view.setPaletteRange([-30.0,60.0])
    view.setTimestepDelta(10)
    view.setLogicToPhysic([(0.0,1.0), (0.0,1.0), (0.0,10.0)])
    view.setDirections({'Long':0,'Lat':1,'Depth':2})
    return pn.Column(view.getMainLayout(),sizing_mode="stretch_width",height=height)
    
app=MyApp()
app

Column(height=800, sizing_mode='stretch_width')
    [0] Column(sizing_mode='stretch_both')
        [0] Column(sizing_mode='stretch_both')
            [0] Row(sizing_mode='stretch_width')
                [0] Row(sizing_mode='stretch_width')
                    [0] MenuButton(button_type='primary', items=[['Load/Save', ...], name='File', width=120)
                    [1] TextInput(sizing_mode='stretch_width', visible=False)
                [1] Select(name='view Mode', options=['1', 'probe', ...], value='1', width=80)
                [2] Select(name='Dataset', options=['0', '1', '2', ...], value='0', width=180)
                [3] EditableFloatSlider(end=10269, format=NumeralTickFormatter(id='1..., name='Time', sizing_mode='stretch_width', start=1, step=1, value=1)
                [4] Select(name='Speed', options=['1x', '2x', '4x', ...], value='1x', width=60)
                [5] Select(name='Field', options=['u'], value='u', width=80)
                [6] ColorMap(name='Palette', ncols=5, options={'Blues256': ('#08306b', ...}, sizing_mode='stretch_width', value=('#30123b', '#311542', ..., value_name='Turbo256')
                [7] Select(name='Mapper', options=['linear', 'log'], value='linear', width=80)
                [8] IntSlider(end=28, name='Max Res', sizing_mode='stretch_width', start=20, value=25)
                [9] Checkbox(name='Auto Res', sizing_mode='stretch_width', value=True)
                [10] IntSlider(end=4, name='#Ref', value=2, width=80)
                [11] TextInput(sizing_mode='stretch_width', visible=False)
            [1] GridBox(ncols=1, sizing_mode='stretch_both')
                [0] Row(sizing_mode='stretch_both')
                    [0] Column(sizing_mode='stretch_both')
                        [0] Row(sizing_mode='stretch_width')
                            [0] Select(name='Direction', options={'Long': 0, 'Lat': 1, ...}, value=2, width=80)
                            [1] EditableFloatSlider(end=51, format=NumeralTickFormatter(id='7..., name='Offset', sizing_mode='stretch_width', step=1, value=26)
                            [2] Select(name='Range', options=['metadata', 'user', ...], value='dynamic-acc', width=120)
                            [3] FloatInput(disabled=True, name='Min', value=-30.0, width=80)
                            [4] FloatInput(disabled=True, name='Max', value=60.0, width=80)
                        [1] Row(sizing_mode='stretch_both')
                            [0] Row(sizing_mode='stretch_both')
                                [0] Bokeh(figure, sizing_mode='stretch_width')
                        [2] Row(sizing_mode='stretch_width')
                            [0] TextInput(sizing_mode='stretch_width')
                            [1] TextInput(sizing_mode='stretch_width')
                    [1] Column(sizing_mode='stretch_both', visible=False)
                        [0] Row(sizing_mode='stretch_width')
                            [0] EditableFloatSlider(format=NumeralTickFormatter(id='4..., name='X coordinate', step=1.0, width=160)
                            [1] EditableFloatSlider(format=NumeralTickFormatter(id='a..., name='Y coordinate', step=1, width=160)
                            [2] EditableRangeSlider(format=NumeralTickFormatter(id='9..., name='Range', width=250)
                            [3] RadioButtonGroup(options=['avg', 'mM', 'med', '*'], sizing_mode='stretch_width', value='avg')
                            [4] IntSlider(end=99, name='Res', start=20, value=24, width=100)
                            [5] IntSlider(end=8, name='#x', start=1, value=2, width=80)
                            [6] IntSlider(end=8, name='#y', start=1, value=2, width=80)
                        [1] Row(sizing_mode='stretch_width')
                            [0] Button(name='lime', sizing_mode='stretch_width')
                            [1] Button(name='red', sizing_mode='stretch_width')
                            [2] Button(name='green', sizing_mode='stretch_width')
                 